# Adapting the 2nd Place Solution of the 2021 NCAAW Competition

- Solution write-up is available here : https://www.kaggle.com/c/ncaaw-march-mania-2021/discussion/230705
- 2nd place code : https://www.kaggle.com/theoviel/2nd-place-ncaaw-2021?scriptVersionId=58780991
- It was adapted from this notebook : https://www.kaggle.com/theoviel/ncaa-starter-the-simpler-the-better 


  - Version 6: Women
  - Version 10: Men

## Config

In [1]:
BASE_PATH = "./data/MDataFiles_Stage1/"
RESULTS_NAME = "MNCAATourneyDetailedResults.csv"
SEED_NAME = "MNCAATourneySeeds.csv"
RANK_NAME = "MMasseyOrdinals.csv"
TEST_NAME = "MSampleSubmissionStage1.csv"

model_type = 'Autolgbm'
message = 'baseline'

train_filename = "./train_#10-book1.csv"
output = "./output/#10-book1"
test_filename = "./test_#10-book1.csv"
task = None
targets = ['WinA']
features = None
categorical_features = None
use_gpu = True
num_folds = 5
seed = 42
num_trials = 10000
time_limit = 7200
fast = False

TEST = False

In [2]:
import os
import re
import sklearn
import numpy as np 
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt

from collections import Counter
from sklearn.metrics import *
from sklearn.linear_model import *
from sklearn.model_selection import *
from autolgbm import AutoLGBM
import pickle

pd.set_option('display.max_columns', None)

In [3]:
# DATA_PATH = '../input/mens-march-mania-2022/MDataFiles_Stage1/'
DATA_PATH = './data/MDataFiles_Stage1/'

for filename in os.listdir(DATA_PATH):
    print(filename)

MNCAATourneyDetailedResults.csv
MSecondaryTourneyTeams.csv
MMasseyOrdinals.csv
MNCAATourneyCompactResults.csv
MNCAATourneySeedRoundSlots.csv
MRegularSeasonDetailedResults.csv
MTeamCoaches.csv
MNCAATourneySeeds.csv
MSecondaryTourneyCompactResults.csv
MConferenceTourneyGames.csv
MSampleSubmissionStage1.csv
MTeamSpellings.csv
Cities.csv
Conferences.csv
MRegularSeasonCompactResults.csv
MSeasons.csv
MTeamConferences.csv
MNCAATourneySlots.csv
MGameCities.csv
MTeams.csv


# Data preparation

## Seeds
> This file identifies the seeds for all teams in each NCAA® tournament, for all seasons of historical data. Thus, there are between 64-68 rows for each year, depending on whether there were any play-in games and how many there were. In recent years the structure has settled at 68 total teams, with four "play-in" games leading to the final field of 64 teams entering Round 1 on Thursday of the first week (by definition, that is DayNum=136 each season). We will not know the seeds of the respective tournament teams, or even exactly which 68 teams it will be, until Selection Sunday on March 15, 2020 (DayNum=132).

> The seed is a 3/4-character :
- First character : Region (W, X, Y, or Z)
- Next two digits : Seed within the region (01 to 16)
- Last character (optional): Distinguishes teams between play-ins ( a or b)

In [4]:
df_seeds = pd.read_csv(DATA_PATH + "MNCAATourneySeeds.csv")
df_seeds.head()

Season Seed  TeamID
0    1985  W01    1207
1    1985  W02    1210
2    1985  W03    1228
3    1985  W04    1260
4    1985  W05    1374

## Season results
> This file identifies the game-by-game results for many seasons of historical data, starting with the 1985 season (the first year the NCAA® had a 64-team tournament). For each season, the file includes all games played from DayNum 0 through 132. It is important to realize that the "Regular Season" games are simply defined to be all games played on DayNum=132 or earlier (DayNum=132 is Selection Sunday, and there are always a few conference tournament finals actually played early in the day on Selection Sunday itself). Thus a game played on or before Selection Sunday will show up here whether it was a pre-season tournament, a non-conference game, a regular conference game, a conference tournament game, or whatever.

In [5]:
df_season_results = pd.read_csv(DATA_PATH + "MRegularSeasonCompactResults.csv")
df_season_results.drop(['NumOT', 'WLoc'], axis=1, inplace=True)

In [6]:
df_season_results['ScoreGap'] = df_season_results['WScore'] - df_season_results['LScore']

In [7]:
df_season_results.head()

Season  DayNum  WTeamID  WScore  LTeamID  LScore  ScoreGap
0    1985      20     1228      81     1328      64        17
1    1985      25     1106      77     1354      70         7
2    1985      25     1112      63     1223      56         7
3    1985      25     1165      70     1432      54        16
4    1985      25     1192      86     1447      74        12

### Features 
For each team at each season, I compute : 
- Number of wins
- Number of losses
- Average score gap of wins
- Average score gap of losses

And use the following features : 
- Win Ratio
- Average score gap

In [8]:
num_win = df_season_results.groupby(['Season', 'WTeamID']).count()
num_win = num_win.reset_index()[['Season', 'WTeamID', 'DayNum']].rename(columns={"DayNum": "NumWins", "WTeamID": "TeamID"})

In [9]:
num_loss = df_season_results.groupby(['Season', 'LTeamID']).count()
num_loss = num_loss.reset_index()[['Season', 'LTeamID', 'DayNum']].rename(columns={"DayNum": "NumLosses", "LTeamID": "TeamID"})

In [10]:
gap_win = df_season_results.groupby(['Season', 'WTeamID']).mean().reset_index()
gap_win = gap_win[['Season', 'WTeamID', 'ScoreGap']].rename(columns={"ScoreGap": "GapWins", "WTeamID": "TeamID"})

In [11]:
gap_loss = df_season_results.groupby(['Season', 'LTeamID']).mean().reset_index()
gap_loss = gap_loss[['Season', 'LTeamID', 'ScoreGap']].rename(columns={"ScoreGap": "GapLosses", "LTeamID": "TeamID"})

Merge

In [12]:
df_features_season_w = df_season_results.groupby(['Season', 'WTeamID']).count().reset_index()[['Season', 'WTeamID']].rename(columns={"WTeamID": "TeamID"})
df_features_season_l = df_season_results.groupby(['Season', 'LTeamID']).count().reset_index()[['Season', 'LTeamID']].rename(columns={"LTeamID": "TeamID"})

In [13]:
df_features_season = pd.concat([df_features_season_w, df_features_season_l], 0).drop_duplicates().sort_values(['Season', 'TeamID']).reset_index(drop=True)

<ipython-input-13-da3452cf3074>:1: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only
  df_features_season = pd.concat([df_features_season_w, df_features_season_l], 0).drop_duplicates().sort_values(['Season', 'TeamID']).reset_index(drop=True)


In [14]:
df_features_season = df_features_season.merge(num_win, on=['Season', 'TeamID'], how='left')
df_features_season = df_features_season.merge(num_loss, on=['Season', 'TeamID'], how='left')
df_features_season = df_features_season.merge(gap_win, on=['Season', 'TeamID'], how='left')
df_features_season = df_features_season.merge(gap_loss, on=['Season', 'TeamID'], how='left')

In [15]:
df_features_season.fillna(0, inplace=True)  

Compute features

In [16]:
df_features_season['WinRatio'] = df_features_season['NumWins'] / (df_features_season['NumWins'] + df_features_season['NumLosses'])
df_features_season['GapAvg'] = (
    (df_features_season['NumWins'] * df_features_season['GapWins'] - 
    df_features_season['NumLosses'] * df_features_season['GapLosses'])
    / (df_features_season['NumWins'] + df_features_season['NumLosses'])
)

In [17]:
df_features_season.drop(['NumWins', 'NumLosses', 'GapWins', 'GapLosses'], axis=1, inplace=True)

## Tourney results

> This file identifies the game-by-game NCAA® tournament results for all seasons of historical data. The data is formatted exactly like the MRegularSeasonCompactResults data. All games will show up as neutral site (so WLoc is always N). Note that this tournament game data also includes the play-in games (which always occurred on day 134/135) for those years that had play-in games. Thus each season you will see between 63 and 67 games listed, depending on how many play-in games there were.

In [18]:
df_tourney_results = pd.read_csv(DATA_PATH + "MNCAATourneyCompactResults.csv")
df_tourney_results.drop(['NumOT', 'WLoc'], axis=1, inplace=True)

## FiveThirtyEight Ratings
> Thanks to Raddar ! https://www.kaggle.com/raddar/ncaa-men-538-team-ratings

In [19]:
df_538 = pd.read_csv("/workspace/data/ncaa-men-538-team-ratings/538ratingsMen.csv")
df_538.drop('TeamName', axis=1, inplace=True)

df_538.head()

Season  TeamID  538rating
0    2016    1242      94.46
1    2016    1314      93.94
2    2016    1438      92.46
3    2016    1277      91.84
4    2016    1328      89.96

# Feature Engineering

## Train data

In [20]:
df = df_tourney_results.copy()
df = df[df['Season'] >= 2016].reset_index(drop=True)

df.head()

Season  DayNum  WTeamID  WScore  LTeamID  LScore
0    2016     134     1195      96     1192      65
1    2016     134     1455      70     1435      50
2    2016     135     1221      59     1380      55
3    2016     135     1276      67     1409      62
4    2016     136     1114      85     1345      83

### Seeds
- `SeedW` is the seed of the winning team
- `SeedL` is the seed of the losing team

In [21]:
df = pd.merge(
    df, 
    df_seeds, 
    how='left', 
    left_on=['Season', 'WTeamID'], 
    right_on=['Season', 'TeamID']
).drop('TeamID', axis=1).rename(columns={'Seed': 'SeedW'})

In [22]:
df = pd.merge(
    df, 
    df_seeds, 
    how='left', 
    left_on=['Season', 'LTeamID'], 
    right_on=['Season', 'TeamID']
).drop('TeamID', axis=1).rename(columns={'Seed': 'SeedL'})

In [23]:
def treat_seed(seed):
    return int(re.sub("[^0-9]", "", seed))

In [24]:
df['SeedW'] = df['SeedW'].apply(treat_seed)
df['SeedL'] = df['SeedL'].apply(treat_seed)

In [25]:
df.head()

Season  DayNum  WTeamID  WScore  LTeamID  LScore  SeedW  SeedL
0    2016     134     1195      96     1192      65     16     16
1    2016     134     1455      70     1435      50     11     11
2    2016     135     1221      59     1380      55     16     16
3    2016     135     1276      67     1409      62     11     11
4    2016     136     1114      85     1345      83     12      5

### Season Stats
- `WinRatioW` is the win ratio of the winning team during the season
- `WinRatioL` is the win ratio of the losing team during the season

In [26]:
df = pd.merge(
    df,
    df_features_season,
    how='left',
    left_on=['Season', 'WTeamID'],
    right_on=['Season', 'TeamID']
).rename(columns={
    'NumWins': 'NumWinsW',
    'NumLosses': 'NumLossesW',
    'GapWins': 'GapWinsW',
    'GapLosses': 'GapLossesW',
    'WinRatio': 'WinRatioW',
    'GapAvg': 'GapAvgW',
}).drop(columns='TeamID', axis=1)

In [27]:
df = pd.merge(
    df,
    df_features_season,
    how='left',
    left_on=['Season', 'LTeamID'],
    right_on=['Season', 'TeamID']
).rename(columns={
    'NumWins': 'NumWinsL',
    'NumLosses': 'NumLossesL',
    'GapWins': 'GapWinsL',
    'GapLosses': 'GapLossesL',
    'WinRatio': 'WinRatioL',
    'GapAvg': 'GapAvgL',
}).drop(columns='TeamID', axis=1)

In [28]:
df.head()

Season  DayNum  WTeamID  WScore  LTeamID  LScore  SeedW  SeedL  WinRatioW  \
0    2016     134     1195      96     1192      65     16     16   0.551724   
1    2016     134     1455      70     1435      50     11     11   0.741935   
2    2016     135     1221      59     1380      55     16     16   0.424242   
3    2016     135     1276      67     1409      62     11     11   0.636364   
4    2016     136     1114      85     1345      83     12      5   0.870968   

     GapAvgW  WinRatioL    GapAvgL  
0   2.724138   0.548387  -1.677419  
1  13.709677   0.593750   9.406250  
2  -4.333333   0.612903   1.870968  
3   6.242424   0.645161   4.322581  
4   9.935484   0.764706  13.147059

### FiveThirtyEight Ratings
- `538ratingW` is the rating of the winning team during the season
- `538ratingL` is the rating of the losing team during the season

In [29]:
df = pd.merge(
    df,
    df_538,
    how='left',
    left_on=['Season', 'WTeamID'],
    right_on=['Season', 'TeamID']
).drop('TeamID', axis=1).rename(columns={'538rating': '538ratingW'})

In [30]:
df = pd.merge(
    df, 
    df_538, 
    how='left', 
    left_on=['Season', 'LTeamID'], 
    right_on=['Season', 'TeamID']
).drop('TeamID', axis=1).rename(columns={'538rating': '538ratingL'})

In [31]:
df.head()

Season  DayNum  WTeamID  WScore  LTeamID  LScore  SeedW  SeedL  WinRatioW  \
0    2016     134     1195      96     1192      65     16     16   0.551724   
1    2016     134     1455      70     1435      50     11     11   0.741935   
2    2016     135     1221      59     1380      55     16     16   0.424242   
3    2016     135     1276      67     1409      62     11     11   0.636364   
4    2016     136     1114      85     1345      83     12      5   0.870968   

     GapAvgW  WinRatioL    GapAvgL  538ratingW  538ratingL  
0   2.724138   0.548387  -1.677419       71.41       66.72  
1  13.709677   0.593750   9.406250       86.59       85.59  
2  -4.333333   0.612903   1.870968       66.85       67.96  
3   6.242424   0.645161   4.322581       79.57       79.93  
4   9.935484   0.764706  13.147059       78.90       88.68

### Add symetrical
- Right now our data only consists of won matches
- We duplicate our data, get rid of the winner loser 

In [32]:
def add_loosing_matches(df):
    win_rename = {
        "WTeamID": "TeamIdA", 
        "WScore" : "ScoreA", 
        "LTeamID" : "TeamIdB",
        "LScore": "ScoreB",
     }
    win_rename.update({c : c[:-1] + "A" for c in df.columns if c.endswith('W')})
    win_rename.update({c : c[:-1] + "B" for c in df.columns if c.endswith('L')})
    
    lose_rename = {
        "WTeamID": "TeamIdB", 
        "WScore" : "ScoreB", 
        "LTeamID" : "TeamIdA",
        "LScore": "ScoreA",
    }
    lose_rename.update({c : c[:-1] + "B" for c in df.columns if c.endswith('W')})
    lose_rename.update({c : c[:-1] + "A" for c in df.columns if c.endswith('L')})
    
    win_df = df.copy()
    lose_df = df.copy()
    
    win_df = win_df.rename(columns=win_rename)
    lose_df = lose_df.rename(columns=lose_rename)
    
    return pd.concat([win_df, lose_df], 0, sort=False)

In [33]:
df = add_loosing_matches(df)

<ipython-input-32-cb2d6ccb7e29>:26: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only
  return pd.concat([win_df, lose_df], 0, sort=False)


In [34]:
df.head()

Season  DayNum  TeamIdA  ScoreA  TeamIdB  ScoreB  SeedA  SeedB  WinRatioA  \
0    2016     134     1195      96     1192      65     16     16   0.551724   
1    2016     134     1455      70     1435      50     11     11   0.741935   
2    2016     135     1221      59     1380      55     16     16   0.424242   
3    2016     135     1276      67     1409      62     11     11   0.636364   
4    2016     136     1114      85     1345      83     12      5   0.870968   

     GapAvgA  WinRatioB    GapAvgB  538ratingA  538ratingB  
0   2.724138   0.548387  -1.677419       71.41       66.72  
1  13.709677   0.593750   9.406250       86.59       85.59  
2  -4.333333   0.612903   1.870968       66.85       67.96  
3   6.242424   0.645161   4.322581       79.57       79.93  
4   9.935484   0.764706  13.147059       78.90       88.68

### Differences
- We compute the difference between the team for each feature.
- This helps further assessing how better (or worse) team A is from team B

In [35]:
cols_to_diff = [
    'Seed', 'WinRatio', 'GapAvg', '538rating'
]

for col in cols_to_diff:
    df[col + 'Diff'] = df[col + 'A'] - df[col + 'B']

## Test Data

### Preparing

In [36]:
df_test = pd.read_csv(DATA_PATH + "MSampleSubmissionStage1.csv")

In [37]:
df_test['Season'] = df_test['ID'].apply(lambda x: int(x.split('_')[0]))
df_test['TeamIdA'] = df_test['ID'].apply(lambda x: int(x.split('_')[1]))
df_test['TeamIdB'] = df_test['ID'].apply(lambda x: int(x.split('_')[2]))

In [38]:
df_test.head()

ID  Pred  Season  TeamIdA  TeamIdB
0  2016_1112_1114   0.5    2016     1112     1114
1  2016_1112_1122   0.5    2016     1112     1122
2  2016_1112_1124   0.5    2016     1112     1124
3  2016_1112_1138   0.5    2016     1112     1138
4  2016_1112_1139   0.5    2016     1112     1139

### Seeds

In [39]:
df_test = pd.merge(
    df_test,
    df_seeds,
    how='left',
    left_on=['Season', 'TeamIdA'],
    right_on=['Season', 'TeamID']
).drop('TeamID', axis=1).rename(columns={'Seed': 'SeedA'})

In [40]:
df_test = pd.merge(
    df_test, 
    df_seeds, 
    how='left', 
    left_on=['Season', 'TeamIdB'], 
    right_on=['Season', 'TeamID']
).drop('TeamID', axis=1).rename(columns={'Seed': 'SeedB'})

In [41]:
df_test['SeedA'] = df_test['SeedA'].apply(treat_seed)
df_test['SeedB'] = df_test['SeedB'].apply(treat_seed)

### Season Stats

In [42]:
df_test = pd.merge(
    df_test,
    df_features_season,
    how='left',
    left_on=['Season', 'TeamIdA'],
    right_on=['Season', 'TeamID']
).rename(columns={
    'NumWins': 'NumWinsA',
    'NumLosses': 'NumLossesA',
    'GapWins': 'GapWinsA',
    'GapLosses': 'GapLossesA',
    'WinRatio': 'WinRatioA',
    'GapAvg': 'GapAvgA',
}).drop(columns='TeamID', axis=1)

In [43]:
df_test = pd.merge(
    df_test,
    df_features_season,
    how='left',
    left_on=['Season', 'TeamIdB'],
    right_on=['Season', 'TeamID']
).rename(columns={
    'NumWins': 'NumWinsB',
    'NumLosses': 'NumLossesB',
    'GapWins': 'GapWinsB',
    'GapLosses': 'GapLossesB',
    'WinRatio': 'WinRatioB',
    'GapAvg': 'GapAvgB',
}).drop(columns='TeamID', axis=1)

### Ratings

In [44]:
df_test = pd.merge(
    df_test,
    df_538,
    how='left',
    left_on=['Season', 'TeamIdA'],
    right_on=['Season', 'TeamID']
).drop('TeamID', axis=1).rename(columns={'538rating': '538ratingA'})

In [45]:
df_test = pd.merge(
    df_test,
    df_538,
    how='left',
    left_on=['Season', 'TeamIdB'],
    right_on=['Season', 'TeamID']
).drop('TeamID', axis=1).rename(columns={'538rating': '538ratingB'})

### Differences

In [46]:
for col in cols_to_diff:
    df_test[col + 'Diff'] = df_test[col + 'A'] - df_test[col + 'B']

In [47]:
df_test.head()

ID  Pred  Season  TeamIdA  TeamIdB  SeedA  SeedB  WinRatioA  \
0  2016_1112_1114   0.5    2016     1112     1114      6     12   0.757576   
1  2016_1112_1122   0.5    2016     1112     1122      6     16   0.757576   
2  2016_1112_1124   0.5    2016     1112     1124      6      5   0.757576   
3  2016_1112_1138   0.5    2016     1112     1138      6     14   0.757576   
4  2016_1112_1139   0.5    2016     1112     1139      6      9   0.757576   

     GapAvgA  WinRatioB   GapAvgB  538ratingA  538ratingB  SeedDiff  \
0  12.212121   0.870968  9.935484       89.04       78.90        -6   
1  12.212121   0.484848 -2.363636       89.04       68.83       -10   
2  12.212121   0.656250  6.687500       89.04       85.47         1   
3  12.212121   0.575758  0.666667       89.04       75.66        -8   
4  12.212121   0.677419  9.419355       89.04       84.17        -3   

   WinRatioDiff  GapAvgDiff  538ratingDiff  
0     -0.113392    2.276637          10.14  
1      0.272727   14.575758          20.21  
2      0.101326    5.524621           3.57  
3      0.181818   11.545455          13.38  
4      0.080156    2.792766           4.87

## Target

In [48]:
df['ScoreDiff'] = df['ScoreA'] - df['ScoreB']
df['WinA'] = (df['ScoreDiff'] > 0).astype(int)

# Modeling

In [49]:
features = [
    'SeedDiff',
    '538ratingDiff',
    'WinRatioDiff', 
    'GapAvgDiff', 
]

In [50]:
def rescale(features, df_train, df_val, df_test=None):
    min_ = df_train[features].min()
    max_ = df_train[features].max()
    
    df_train[features] = (df_train[features] - min_) / (max_ - min_)
    df_val[features] = (df_val[features] - min_) / (max_ - min_)
    
    if df_test is not None:
        df_test[features] = (df_test[features] - min_) / (max_ - min_)
        
    return df_train, df_val, df_test

### Cross Validation
- Validate on season `n`, for `n` in the 3 last seasons. 
- Train on earlier seasons. First available season is 2016 because of the FiveThirtyEight ratings.
- Pipeline support classification (predict the team that wins) and regression (predict the score gap), but classification worked better on CV.

In [51]:
def kfold(df, df_test_=None, plot=False, verbose=0, mode="reg"):
    seasons = df['Season'].unique()
    cvs = []
    pred_tests = []
    target = "ScoreDiff" if mode == "reg" else "WinA"
    
    for season in seasons[1:]:
        if verbose:
            print(f'\nValidating on season {season}')
        
        df_train = df[df['Season'] < season].reset_index(drop=True).copy()
        df_val = df[df['Season'] == season].reset_index(drop=True).copy()
        df_test = df_test_.copy()
        
        df_train, df_val, df_test = rescale(features, df_train, df_val, df_test)
        
        if mode == "reg":
            model = ElasticNet(alpha=1, l1_ratio=0.5)
        else:
            model = LogisticRegression(C=100,max_iter=1000000)

        model.fit(df_train[features], df_train[target])
        
        if mode == "reg":
            pred = model.predict(df_val[features])
            pred = (pred - pred.min()) / (pred.max() - pred.min())
        else:
            pred = model.predict_proba(df_val[features])[:, 1]
        
        if df_test is not None:
            if mode == "reg":
                pred_test = model.predict(df_test[features])
                pred_test = (pred_test - pred_test.min()) / (pred_test.max() - pred_test.min())
            else:
                pred_test = model.predict_proba(df_test[features])[:, 1]
                
            pred_tests.append(pred_test)
            
        if plot:
            plt.figure(figsize=(15, 6))
            plt.subplot(1, 2, 1)
            plt.scatter(pred, df_val['ScoreDiff'].values, s=5)
            plt.grid(True)
            plt.subplot(1, 2, 2)
            sns.histplot(pred)
            plt.show()
        
        loss = log_loss(df_val['WinA'].values, pred)
        cvs.append(loss)

        if verbose:
            print(f'\t -> Scored {loss:.3f}')
        
    print(f'\n Local CV is {np.mean(cvs):.3f}')
    
    return pred_tests

In [52]:
df_ = df.drop(['DayNum','ScoreDiff','ScoreA','ScoreB'],axis=1)
df_test_ = df_test.drop(['ID', 'Pred'], axis=1)
len(df_.columns)

16

In [54]:
import re
import warnings
scaled_df, scaled_df_test, _ = rescale(features, \
    df_.rename(columns=lambda x: re.sub('[^A-Za-z0-9_]+', '', x)), \
        df_test_.rename(columns=lambda x: re.sub('[^A-Za-z0-9_]+', '', x)))
# scaled_df = scaled_df.rename(columns=lambda x: re.sub('[^A-Za-z0-9_]+', '', x))
# scaled_df_test = scaled_df_test.rename(columns = lambda x:re.sub('[^A-Za-z0-9_]+', '', x))
scaled_df.iloc[:,1:].to_csv(train_filename,index=None)
scaled_df_test.iloc[:, 1:].to_csv(test_filename,index=None)
# scaled_df.columns[2:].values
warnings.simplefilter('ignore')
model = AutoLGBM(
    train_filename=train_filename,
    output=output,
    test_filename=test_filename,
    task=task,
    targets=targets,
    features=None, # features,
    categorical_features=categorical_features,
    use_gpu=use_gpu,
    num_folds=num_folds,
    seed=seed,
    num_trials=num_trials,
    time_limit=time_limit,
    fast=fast,
    
)
model.train()
print('finished training...')
filename = "./output/#10-book1_model.pickle"
with open(filename, 'bw') as f:
    pickle.dump(model, f)


2022-03-13 11:07:24.019 | INFO     | autolgbm.autolgbm:__post_init__:42 - Output directory: ./output/#10-book1
2022-03-13 11:07:24.020 | INFO     | autolgbm.autolgbm:_process_data:149 - Reading training data
2022-03-13 11:07:24.029 | INFO     | autolgbm.utils:reduce_memory_usage:48 - Mem. usage decreased to 0.02 Mb (77.4% reduction)
2022-03-13 11:07:24.030 | INFO     | autolgbm.autolgbm:_determine_problem_type:140 - Problem type: binary_classification
2022-03-13 11:07:24.048 | INFO     | autolgbm.utils:reduce_memory_usage:48 - Mem. usage decreased to 0.28 Mb (76.8% reduction)
2022-03-13 11:07:24.049 | INFO     | autolgbm.autolgbm:_create_folds:58 - Creating folds
2022-03-13 11:07:24.052 | INFO     | autolgbm.autolgbm:_process_data:170 - Encoding target(s)
2022-03-13 11:07:24.055 | INFO     | autolgbm.autolgbm:_process_data:195 - Found 0 categorical features.
2022-03-13 11:07:24.103 | INFO     | autolgbm.autolgbm:_process_data:236 - Model config: train_filename='./train_#10-book1.csv' t

[LightGBM] [Warning] lambda_l1 is set=4.403155624438042, reg_alpha=0.0 will be ignored. Current value: lambda_l1=4.403155624438042
[LightGBM] [Warning] bagging_fraction is set=0.7139159354498734, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7139159354498734
[LightGBM] [Warning] feature_fraction is set=0.7013742412270205, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.7013742412270205
[LightGBM] [Warning] bagging_freq is set=6, subsample_freq=0 will be ignored. Current value: bagging_freq=6
[LightGBM] [Warning] lambda_l2 is set=1.0377176533705759e-06, reg_lambda=0.0 will be ignored. Current value: lambda_l2=1.0377176533705759e-06
[LightGBM] [Warning] lambda_l1 is set=4.403155624438042, reg_alpha=0.0 will be ignored. Current value: lambda_l1=4.403155624438042
[LightGBM] [Warning] bagging_fraction is set=0.7139159354498734, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7139159354498734
[LightGBM] [Warning] feature_fraction is

2022-03-13 11:07:44.125 | INFO     | autolgbm.utils:optimize:191 - Metrics: {'auc': 0.7813547594456483, 'binary_logloss': 0.5680141875523744, 'f1': 0.6895249296430624, 'accuracy': 0.700639658848614, 'precision': 0.716098813930649, 'recall': 0.667706919945726}
[I 2022-03-13 11:07:44,166] Trial 0 finished with value: 0.5680141875523744 and parameters: {'learning_rate': 0.09512088513506949, 'max_depth': 5, 'early_stopping_rounds': 374, 'n_estimators': 7000, 'lambda_l1': 4.403155624438042, 'lambda_l2': 1.0377176533705759e-06, 'num_leaves': 240, 'feature_fraction': 0.7013742412270205, 'bagging_fraction': 0.7139159354498734, 'bagging_freq': 6, 'min_child_samples': 67}. Best is trial 0 with value: 0.5680141875523744.


[LightGBM] [Warning] lambda_l1 is set=3.1626135403642057, reg_alpha=0.0 will be ignored. Current value: lambda_l1=3.1626135403642057
[LightGBM] [Warning] bagging_fraction is set=0.9937315180440822, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9937315180440822
[LightGBM] [Warning] feature_fraction is set=0.43813580812446207, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.43813580812446207
[LightGBM] [Warning] bagging_freq is set=4, subsample_freq=0 will be ignored. Current value: bagging_freq=4
[LightGBM] [Warning] lambda_l2 is set=9.959877896887495e-05, reg_lambda=0.0 will be ignored. Current value: lambda_l2=9.959877896887495e-05
[LightGBM] [Warning] lambda_l1 is set=3.1626135403642057, reg_alpha=0.0 will be ignored. Current value: lambda_l1=3.1626135403642057
[LightGBM] [Warning] bagging_fraction is set=0.9937315180440822, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9937315180440822
[LightGBM] [Warning] feature_fractio

2022-03-13 11:08:00.705 | INFO     | autolgbm.utils:optimize:191 - Metrics: {'auc': 0.7730836995483911, 'binary_logloss': 0.5724447925124683, 'f1': 0.6963230387277497, 'accuracy': 0.6990461227696106, 'precision': 0.7037940364915176, 'recall': 0.6917232021709634}
[I 2022-03-13 11:08:00,744] Trial 1 finished with value: 0.5724447925124683 and parameters: {'learning_rate': 0.048634653195059954, 'max_depth': 7, 'early_stopping_rounds': 265, 'n_estimators': 7000, 'lambda_l1': 3.1626135403642057, 'lambda_l2': 9.959877896887495e-05, 'num_leaves': 89, 'feature_fraction': 0.43813580812446207, 'bagging_fraction': 0.9937315180440822, 'bagging_freq': 4, 'min_child_samples': 81}. Best is trial 0 with value: 0.5680141875523744.


...

[LightGBM] [Warning] Unknown parameter: predictor
[LightGBM] [Warning] Unknown parameter: tree_method
[LightGBM] [Warning] Unknown parameter: gpu_id
[LightGBM] [Warning] feature_fraction is set=0.9893147688147023, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9893147688147023
[LightGBM] [Warning] lambda_l1 is set=0.08151923461839221, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.08151923461839221
[LightGBM] [Warning] bagging_fraction is set=0.883609639902179, subsample=1.0 will be ignored. Current value: bagging_fraction=0.883609639902179
[LightGBM] [Warning] bagging_freq is set=3, subsample_freq=0 will be ignored. Current value: bagging_freq=3
[LightGBM] [Warning] lambda_l2 is set=2.158160763209973e-08, reg_lambda=0.0 will be ignored. Current value: lambda_l2=2.158160763209973e-08


2022-03-13 13:07:33.256 | INFO     | autolgbm.utils:predict_model:331 - Fold 3 done!
2022-03-13 13:07:33.256 | INFO     | autolgbm.utils:predict_model:237 - Training and predicting for fold 4


[LightGBM] [Warning] Unknown parameter: predictor
[LightGBM] [Warning] Unknown parameter: tree_method
[LightGBM] [Warning] Unknown parameter: gpu_id
[LightGBM] [Warning] feature_fraction is set=0.9893147688147023, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9893147688147023
[LightGBM] [Warning] lambda_l1 is set=0.08151923461839221, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.08151923461839221
[LightGBM] [Warning] bagging_fraction is set=0.883609639902179, subsample=1.0 will be ignored. Current value: bagging_fraction=0.883609639902179
[LightGBM] [Warning] bagging_freq is set=3, subsample_freq=0 will be ignored. Current value: bagging_freq=3
[LightGBM] [Warning] lambda_l2 is set=2.158160763209973e-08, reg_lambda=0.0 will be ignored. Current value: lambda_l2=2.158160763209973e-08


2022-03-13 13:07:34.709 | INFO     | autolgbm.utils:predict_model:331 - Fold 4 done!
2022-03-13 13:07:34.718 | INFO     | autolgbm.utils:predict_model:334 - Metrics: {'auc': 0.7869289914066033, 'binary_logloss': 0.551128930559996, 'f1': 0.7039485524256651, 'accuracy': 0.7096173268993379, 'precision': 0.7183077199990913, 'recall': 0.6978742650384442}


finished training...


In [55]:
model

AutoLGBM(train_filename='./train_#10-book1.csv', output='./output/#10-book1', test_filename='./test_#10-book1.csv', task=None, idx='id', targets=['WinA'], features=['TeamIdA', 'TeamIdB', 'SeedA', 'SeedB', 'WinRatioA', 'GapAvgA', 'WinRatioB', 'GapAvgB', '538ratingA', '538ratingB', 'SeedDiff', 'WinRatioDiff', 'GapAvgDiff', '538ratingDiff'], categorical_features=None, use_gpu=True, num_folds=5, seed=42, num_trials=10000, time_limit=7200, fast=False)

In [ ]:
# pred_tests = kfold(df, df_test, plot=True, verbose=1, mode="cls")
# pred_test = np.mean(pred_tests, 0)

# _ = sns.displot(pred_test)


# Overriding predictions
- Without overridees, the 4 features model achieved 22nd, which is good but enough !

## Prepare

In [53]:
sub = df_test[['ID', 'Season', 'Pred', 'TeamIdA', 'TeamIdB', 'SeedA', 'SeedB']].copy()
sub['Pred'] = pred_test

In [54]:
df_teams = pd.read_csv(DATA_PATH + "MTeams.csv")
sub = sub.merge(df_teams, left_on="TeamIdA", right_on="TeamID").drop('TeamID', axis=1).rename(columns={"TeamName": "TeamA"})
sub = sub.merge(df_teams, left_on="TeamIdB", right_on="TeamID").drop('TeamID', axis=1).rename(columns={"TeamName": "TeamB"})

In [55]:
df_seeds['Seed'] = df_seeds['Seed'].apply(lambda x:x[0])

sub = sub.merge(df_seeds, left_on=["TeamIdA", "Season"], right_on=["TeamID", "Season"]).drop('TeamID', axis=1).rename(columns={"Seed": "RegionA"})
sub = sub.merge(df_seeds, left_on=["TeamIdB", "Season"], right_on=["TeamID", "Season"]).drop('TeamID', axis=1).rename(columns={"Seed": "RegionB"})

## Strategies

#### Risky strategy

- Picked 11 teams that would win their first match
- Stanford and Baylor beat every team seeded 3 or higher
- Connecticut and South Carolina  beat every team seeded 4 or higher
- Maryland wins beats every team seeded 7 or higher
- use p=0.99999 for overriding

#### Safe strategy

- Picked 7 teams that would win their first match
- Stanford, Connecticut and South Carolina beat every team seeded 6 or higher
- Baylor wins beats every team seeded 7 or higher
- use p=0.99 for overriding

*This parts needs to be updated using this year's best teams. I'm waiting to get analysts' insights for this.*
Also, this was for the women teams so don't be this aggressive with the men competition as there usually are more upsets.

In [56]:
best_teams = ['Stanford', 'South Carolina', 'Connecticut', 'Baylor', 'Maryland']  # considered for buff

strong_teams_safe = best_teams + ['NC State', 'Louisville']  # win 1st round
strong_teams_risky = strong_teams_safe + ['Texas A&M', 'Arizona', 'Georgia', 'UCLA']  # win 1st round

In [57]:
def overwrite_pred_risky(sub, eps=1e-5):

    new_sub = []
    
    for i, row in sub.iterrows():
        
        # Buff Stanford
        if row['TeamA'] == 'Stanford' and row['SeedB'] >= 3:
            row['Pred'] = 1 - eps
        elif row['TeamB'] == 'Stanford' and row['SeedA'] >= 3:
            row['Pred'] = eps
    
        # Buff South Carolina
        if row['TeamA'] == 'South Carolina' and row['SeedB'] >= 4:
            row['Pred'] = 1 - eps
        elif row['TeamB'] == 'South Carolina' and row['SeedA'] >= 4:
            row['Pred'] = eps
            
        # Buff Connecticut
        if row['TeamA'] == 'Connecticut' and row['SeedB'] >= 4:
            row['Pred'] = 1 - eps
        elif row['TeamB'] == 'Connecticut' and row['SeedA'] >= 4:
            row['Pred'] = eps
            
        # Buff Baylor
        if row['TeamA'] == 'Baylor' and row['SeedB'] >= 3:
            row['Pred'] = 1 - eps
        elif row['TeamB'] == 'Baylor' and row['SeedA'] >= 3:
            row['Pred'] = eps
            
        # Buff Maryland
        if row['TeamA'] == 'Maryland' and row['SeedB'] >= 7:
            row['Pred'] = 1 - eps
        elif row['TeamB'] == 'Maryland' and row['SeedA'] >= 7:
            row['Pred'] = eps
        
        # Strong teams (risky) win their first round
        if row['TeamA'] in strong_teams_risky and row['SeedB'] >= 13:
            row['Pred'] = 1 - eps
        elif row['TeamB'] in strong_teams_risky and row['SeedA'] >= 13:
            row['Pred'] = eps

        new_sub.append(row)
        
    return pd.DataFrame(np.array(new_sub), columns=sub.columns)

In [58]:
def overwrite_pred_safe(sub, eps=1e-2):    
    new_sub = []
    
    for i, row in sub.iterrows():
        row['Pred'] = np.clip(row['Pred'], 0.1, 0.9) # clip for safety
        
        # Buff Stanford
        if row['TeamA'] == 'Stanford' and row['SeedB'] >= 6:
            row['Pred'] = 1 - eps
        elif row['TeamB'] == 'Stanford' and row['SeedA'] >= 6:
            row['Pred'] = eps
    
        # Buff South Carolina
        if row['TeamA'] == 'South Carolina' and row['SeedB'] >= 6:
            row['Pred'] = 1 - eps
        elif row['TeamB'] == 'South Carolina' and row['SeedA'] >= 6:
            row['Pred'] = eps
            
        # Buff Connecticut
        if row['TeamA'] == 'Connecticut' and row['SeedB'] >= 6:
            row['Pred'] = 1 - eps
        elif row['TeamB'] == 'Connecticut' and row['SeedA'] >= 6:
            row['Pred'] = eps

        # Buff Baylor
        if row['TeamA'] == 'Baylor' and row['SeedB'] >= 7:
            row['Pred'] = 1 - eps
        elif row['TeamB'] == 'Baylor' and row['SeedA'] >= 7:
            row['Pred'] = eps
        
        # Strong teams (safe) win their first rounds
        if row['TeamA'] in strong_teams_safe and row['SeedB'] >= 13:
            row['Pred'] = 1 - eps
        elif row['TeamB'] in strong_teams_safe and row['SeedA'] >= 13:
            row['Pred'] = eps

        new_sub.append(row)
        
    return pd.DataFrame(np.array(new_sub), columns=sub.columns)

## Submission

In [56]:
SAVE_DIR = './output/'

In [68]:
# sub_pp = overwrite_pred_safe(sub)
# sub_pp = overwrite_pred_risky(sub)

sub_pp = sub

final_sub = sub_pp[['ID', 'Pred']].copy()
final_sub.to_csv(SAVE_DIR + '#10_submission_with_auto-lgbm.csv', index=False)
final_sub.head()


In [57]:
submission = pd.read_csv(BASE_PATH + "MSampleSubmissionStage1.csv")
autolgb_pred = pd.read_csv(output+"/test_predictions.csv")
submission['Pred'] = autolgb_pred['1']
# submission.rename(columns = {'1.0':'Pred'}, inplace = True)
submission.to_csv(SAVE_DIR + "#10-book1_submission.csv", index=False)
submission.head()


ID      Pred
0  2016_1112_1114  0.804757
1  2016_1112_1122  0.872533
2  2016_1112_1124  0.651544
3  2016_1112_1138  0.873706
4  2016_1112_1139  0.681486

In [8]:
with open("/workspace/output/#10-book1_model.pickle", "br") as f:
    model = pickle.load(f)
    
model


AutoLGBM(train_filename='./train_#10-book1.csv', output='./output/#10-book1', test_filename='./test_#10-book1.csv', task=None, idx='id', targets=['WinA'], features=['SeedDiff', '538ratingDiff', 'WinRatioDiff', 'GapAvgDiff'], categorical_features=None, use_gpu=True, num_folds=10, seed=42, num_trials=10000, time_limit=7200, fast=False)